Q8)Determine the Top 5 Vehicle Makes where drivers are charged with speeding related offences, has licensed Drivers, used top 10 used vehicle colours and has car licensed with the Top 25 states with highest number of offence

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.window import *

In [0]:
df_charges=spark.read.format("csv").option("inferschema",True).option("header",True).load("dbfs:/FileStore/Charges_use.csv")

A person in the charges dataframe is uniquely identified by (CRASH_ID, UNIT_NBR ,PRSN_NBR)

Filtering charges on the basis over speeding offences

In [0]:
df_charges.filter(col("CHARGE").like("%SPEED%")).orderBy("CRASH_ID","UNIT_NBR","PRSN_NBR","CHARGE").select("CRASH_ID","UNIT_NBR","PRSN_NBR","CHARGE").show()

+--------+--------+--------+--------------------+
|CRASH_ID|UNIT_NBR|PRSN_NBR|              CHARGE|
+--------+--------+--------+--------------------+
|13403990|       1|       1|        UNSAFE SPEED|
|14838834|       1|       1|FAIL TO CONTROL S...|
|14838972|       2|       1|FAIL TO CONTROL S...|
|14838977|       1|       1|        UNSAFE SPEED|
|14839233|       1|       1|        UNSAFE SPEED|
|14839240|       1|       1|FAILED TO CONTROL...|
|14839272|       1|       1|FAIL TO CONTROL S...|
|14839342|       1|       1|FAILED TO CONTROL...|
|14839404|       1|       1|FAILED TO CONTROL...|
|14839510|       1|       1|FAIL TO CONTROL S...|
|14839519|       1|       1|        UNSAFE SPEED|
|14839675|       1|       1|FAIL TO CONTROL S...|
|14839713|       1|       1|FAILURE TO CONTRO...|
|14839721|       1|       1|FAIL TO CONTROL S...|
|14839735|       1|       1|FAILURE TO CONTRO...|
|14839850|       1|       1|        UNSAFE SPEED|
|14839875|       1|       1|FAILED TO CONTROL...|


In [0]:
df_temp1=df_charges.filter(col("CHARGE").like("%SPEED%")).orderBy("CRASH_ID","UNIT_NBR","PRSN_NBR","CHARGE").select("CRASH_ID","UNIT_NBR","PRSN_NBR","CHARGE")

In [0]:
df_temp1.select("PRSN_NBR").distinct().show()

+--------+
|PRSN_NBR|
+--------+
|       1|
+--------+



We see in the above finding that the  PRSN_NBR of all  the people involved in speeding offences is same ( that is 1), in this case we can uniquely indentify the person just by his/her (CRASH_ID ,UNIT_NBR) 

Finding the top 10 used vehicle colors

In [0]:
df_units=spark.read.format("csv").option("inferschema",True).option("header",True).load("dbfs:/FileStore/Units_use.csv")

Checking for undesired values in 'vehicle color ID' column

In [0]:
display(df_units.select("VEH_COLOR_ID").distinct())

VEH_COLOR_ID RED TEA BLK ONG YEL GLD NA 99 CAM BRZ TRQ SIL CPR BRO PLE BLU MAR BGE PNK WHI TAN MUL GRN GRY 98

In [0]:
df_temp2=df_units.filter((col("VEH_COLOR_ID")!="99") & (col("VEH_COLOR_ID")!="98")&(col("VEH_COLOR_ID")!="NA"))

In [0]:
df_temp2.groupBy("VEH_COLOR_ID").count().orderBy(desc("count")).select("VEH_COLOR_ID","count").show()

+------------+-----+
|VEH_COLOR_ID|count|
+------------+-----+
|         WHI|38354|
|         BLK|27749|
|         SIL|20777|
|         GRY|18174|
|         BLU|15471|
|         RED|14095|
|         GRN| 6767|
|         MAR| 6010|
|         TAN| 4846|
|         GLD| 4062|
|         BRO| 2531|
|         BGE| 2200|
|         YEL| 1283|
|         MUL|  966|
|         ONG|  816|
|         PLE|  393|
|         BRZ|  154|
|         TEA|   86|
|         TRQ|   43|
|         PNK|   27|
+------------+-----+
only showing top 20 rows



In [0]:
list_top10_colors=df_temp2.groupBy("VEH_COLOR_ID").count().orderBy(desc("count")).select("VEH_COLOR_ID").limit(10).rdd.flatMap(lambda x:x).collect()

In [0]:
list_top10_colors

Out[246]: ['WHI', 'BLK', 'SIL', 'GRY', 'BLU', 'RED', 'GRN', 'MAR', 'TAN', 'GLD']

Finding the top 25 states with highest number of offences(any)

In [0]:
df_prim_person=spark.read.format("csv").option("inferschema",True).option("header",True).load("dbfs:/FileStore/Primary_Person_use.csv")

In [0]:
df_temp=df_charges.join(df_prim_person,(df_charges.CRASH_ID==df_prim_person.CRASH_ID)&(df_charges.UNIT_NBR==df_prim_person.UNIT_NBR)&(df_charges.PRSN_NBR==df_prim_person.PRSN_NBR))

Checking for undesired value in 'driver license state ID' column

In [0]:
display(df_temp.select("DRVR_LIC_STATE_ID").distinct())

DRVR_LIC_STATE_ID Utah Minnesota Ohio Arkansas Oregon NA Texas North Dakota Pennsylvania Connecticut Nebraska Vermont Nevada Puerto Rico Washington Illinois Oklahoma Unknown Other Alaska New Mexico Missouri Mexico Georgia Montana Michigan Virginia North Carolina Wyoming Kansas New Jersey Maryland Alabama Arizona Iowa Canada Massachusetts Kentucky Louisiana Mississippi Tennessee Florida Indiana Idaho South Carolina California New York Wisconsin Colorado Maine Hawaii American Samoa (Islands) West Virginia South Dakota District of Columbia Delaware Rhode Island Northern Mariana Islands New Hampshire

In [0]:
df_temp=df_temp.filter(col("DRVR_LIC_STATE_ID")!="NA").filter(col("DRVR_LIC_STATE_ID")!="Unknown").filter(col("DRVR_LIC_STATE_ID")!="Other")

In [0]:
df_temp.groupBy("DRVR_LIC_STATE_ID").count().orderBy(desc("count")).show()

+-----------------+-----+
|DRVR_LIC_STATE_ID|count|
+-----------------+-----+
|            Texas|96985|
|           Mexico|  740|
|        Louisiana|  502|
|       New Mexico|  492|
|       California|  455|
|          Florida|  340|
|         Oklahoma|  330|
|         Arkansas|  239|
|          Arizona|  182|
|          Georgia|  147|
|         Illinois|  128|
|      Mississippi|  123|
|         Colorado|  123|
|   North Carolina|  117|
|        Tennessee|  113|
|         Missouri|  110|
|          Alabama|  102|
|           Kansas|   94|
|             Ohio|   83|
|         Michigan|   78|
+-----------------+-----+
only showing top 20 rows



In [0]:
list_top25_states=df_temp.groupBy("DRVR_LIC_STATE_ID").count().orderBy(desc("count")).select("DRVR_LIC_STATE_ID").limit(25).rdd.flatMap(lambda x: x).collect()

In [0]:
list_top25_states

Out[253]: ['Texas',
 'Mexico',
 'Louisiana',
 'New Mexico',
 'California',
 'Florida',
 'Oklahoma',
 'Arkansas',
 'Arizona',
 'Georgia',
 'Illinois',
 'Mississippi',
 'Colorado',
 'North Carolina',
 'Tennessee',
 'Missouri',
 'Alabama',
 'Kansas',
 'Ohio',
 'Michigan',
 'New York',
 'Virginia',
 'Nevada',
 'Washington',
 'South Carolina']

Converting State names into thier abbreviation for future use

In [0]:
list_top25_states = [
    'TX', 'MX', 'LA', 'NM', 'CA', 'FL', 'OK', 'AR', 'AZ', 'GA', 'IL', 'MS', 'CO', 'NC', 'TN',
    'MO', 'AL', 'KS', 'OH', 'MI', 'NY', 'VA', 'NV', 'WA', 'SC'
]

In [0]:
df_restrict=spark.read.format("csv").option("inferschema",True).option("header",True).load("dbfs:/FileStore/Restrict_use.csv")


In [0]:
display(df_restrict.select("DRVR_LIC_RESTRIC_ID").distinct())

DRVR_LIC_RESTRIC_ID MOPED (EFF. END 12/31/2016) APPLICABLE PROSTHETIC DEVICES FRSI CDL MM/DD/YY - MM/DD/YY OR EXEMPT A VEH TRC 545.424 APPLIES UNTIL MM/DD/YY TO/FROM WORK OR LOFS 21 OR OVER INTRASTATE ONLY (EFF. 1/1/2017) WITH CORRECTIVE LENSES STATED ON LICENSE OPERATION CLASS A EXEMPT VEH AUTHORIZED VEHICLE NOT TO EXCEED CLASS C (EFF. END 12/31/2016) NO CLASS A AND B PASSENGER VEHICLE (EFF. 1/1/2017) IF CMV, CUSTOM-HARVESTING INTERSTATE LOFS 21 OR OVER SCHOOL BUS ONLY PASSENGER CMVS RESTRICT TO CLASS C ONLY IF CMV, PRIVATELY TRANS PASSENGERS INTERSTATE OPERATION CLASS B EXEMPT VEH AUTHORIZED LOFS 21 OR OVER VEHICLE ABOVE CLASS C IGNITION INTERLOCK REQUIRED (EFF. END 12/31/2016) LOFS 21 OR OVER IN VEH EQUIP W/ AIRBRAKE BUS NOT TO EXCEED 26,000 LBS GVWR IF CMV, GOVERNMENT VEHICLES INTERSTATE MEDICAL VARIANCE OTHER/OUT OF STATE IF CMV, USE IN OIL/WATER WELL SERVICE/DRILL HME EXPIRATION DATE MM/DD/YY FRSI CDL MM/DD/YY - MM/DD/YY OR EXEMPT B VEH OCC./ESSENT. NEED DL-NO CMV-SEE COURT ORDER (EFF. END 12/31/2016) MUST HOLD VALID LEARNER LIC. TO MM/DD/YY SPEED NOT TO EXCEED 45 MPH LICENSED MC OPERATOR 21 OR OVER IN SIGHT IF CMV, FOR OPERATION OF MOBILE CRANE UNKNOWN TO/FROM WORK/SCHOOL TO/FROM WORK/SCHOOL OR LOFS 21 OR OVER IF CMV, TRANSPORTING BEES/HIVES INTERSTATE NO EXPRESSWAY DRIVING (EFF. END 12/31/2016) VEHICLE NOT TO EXCEED 26,000 LBS GVWR LOFS 21 OR OVER BUS ONLY NO AIR BRAKE EQUIPPED CMV WITH TELESCOPIC LENS IF CMV, TRANS CORPSE/SICK/INJURED INTERSTATE LOFS 21 OR OVER UNLICENSED DAYTIME DRIVING ONLY OTHER CDL INTRASTATE ONLY (EFF. END 12/31/2016) IF CMV, INTRA-CITY ZONE DRIVERS INTERSTATE VALID TX VISION OR LIMB WAIVER REQUIRED FRSI CDL VALID MM/DD/YY TO MM/DD/YY LOFS 21 OR OVER VEHICLE ABOVE CLASS B IF CMV, FIRE/RESCUE INTERSTATE MC NOT TO EXCEED 250 CC NONE IF CMV, SCHOOL BUSES INTERSTATE FOR CLASS M TRC 545.424 UNTIL MM/DD/YY CLASS C ONLY - NO TAXI/BUS/EMERGENCY VEH AUTOMATIC TRANSMISSION IF CMV, ONLY TRANS PERSONAL PROP INTERSTATE OUTSIDE REARVIEWMIRROR OR HEARING AID POWER STEERING TO/FROM WORK APPLICABLE VEHICLE DEVICES (EFF. END 12/31/2016)

In [0]:
df_temp3=df_restrict.filter(col("DRVR_LIC_RESTRIC_ID")!="UNLICENSED")

Checking if there is any undesired value in 'vehicle maker ID' column

In [0]:
display(df_units.select("VEH_MAKE_ID").distinct())

VEH_MAKE_ID AMERICAN IRON HORSE ACURA WHITE MOTOR COACH MND INC PIERCE PORSCHE WHITEGMC FREIGHTLINER BUELL STERLING HYUNDAI INTERNATIONAL PETER PIRSCH & SONS FIAT NA TOYOTA RAM SUBARU NISSAN IC CORPORATION BENTLEY EMERGENCY ONE SUZUKI INFINITI HINO FORD AUDI PREVOST FERRARI ISUZU OLDSMOBILE WESTERN TRUCK & TRAILER CO MINI SAAB DODGE CHEVROLET JAGUAR MCI (LES AUTO BUS) MERCURY LEXUS NORTH AMERICAN BUS JEEP VOLVO GRAYCO JOHN DEERE TESLA DUCATI GM UNKNOWN MAZDA DAEWOO REQUIRES INTERPRETATION BMW MASERATI VOLKSWAGEN GEO PONTIAC EAGLE BLUE BIRD HOMEMADE VEHICLE ALL OTHER MAKES HARLEY-DAVIDSON YAMAHA KIA HUMMER WESTERN STAR HONDA OTHER (EXPLAIN IN NARRATIVE) SATURN KAWASAKI GMC CRANE CARRIER SMART CADILLAC ELDORADO NEW FLYER PLYMOUTH LINCOLN MACK THOMAS CATERPILLAR MURPHY MANUFACTURING CO MERCEDES-BENZ BUICK KENWORTH AUTOCAR CHRYSLER AMERICAN MOTORS LAND ROVER MITSUBISHI PETERBILT UTILIMASTER GILLIG DATSUN CAN-AM COUNTRY COACH FLOE INTERNATIONAL BUGATTI WINNEBAGO SPARTAN WORKHORSE TRI-QUEST INC RENAULT PIAGGIO ORION HYUNDAI STEEL INDUSTRIES NISSAN DIESEL POLARIS OTTAWA AUTOCAR LLC FORETRAVEL INTERMOUNTAIN WHOLE SALE INC VAN HOOL APRILIA NABORS TRAILERS ROLLS-ROYCE ROAD RAILER VICTORY BUS & COACH INTL INTERNATIONAL TRAILER CORP MIDLAND MANUFACTURING LIMITED CHALLENGE-COOK BROTHERS INC FLOW BOY MFG KYMCO INTERNATIONAL TANK & TRAILER CORP FEDERAL MOTORS VESPA INDIAN ASTON MARTIN AM GENERAL U-HAUL INTERNATIONAL HYOSUNG SUPREME CORP GENERAL TRAILER CO EAGLE TRANSIT GALBREATH INC ULTRA LITE MFG NOVA FABRICATING ALFA ROMEO HEIL CO EAGER BEAVER HOGG/DAVIS INC D & B TRAILER MAC LTT UNITED EXPRESS LINE INC NOVA FRUEHAUF MCLAREN MANAC INC BRI-MAR MANUFACTURING LLC INDEPENDENT TRAILER MFG MITSUBISHI FUSO STEPHENS PNEUMATIC LOTUS KENTUCKY MFG WABASH NATIONAL CORP SPARTA MANUFACTURING CORP FEATHERLITE MFG INC

In [0]:
df_temp2=df_units.filter(col("VEH_MAKE_ID")!="NA").filter(col("VEH_MAKE_ID")!="UNKNOWN")

'df_temp1' :  people charged with overspeeding ,  'df_temp3' : licensed people


As discussed before, because the PRSN_NBR of for every record in df_temp1 is same, we can uniquely identify a person just by his/her (CRASH_ID,UNIT_NBR)

Column name change required in 'df_temp1' inorder to avoid ambiguity after join.

In [0]:
df_temp1=df_temp1.withColumnRenamed("CRASH_ID","crash_id_2").withColumnRenamed("UNIT_NBR","unit_nbr_2")

In [0]:
df_temp4=df_temp1.join(df_temp3,(df_temp1.crash_id_2==df_temp3.CRASH_ID)&(df_temp1.unit_nbr_2==df_temp3.UNIT_NBR))

'df_temp2' : vehicle info for all vehicles having valid vehicle maker IDs  ,                              'df_temp4' : all people charged with overspeeding and are license holders 

In [0]:
df_temp5=df_temp4.join(df_temp2,(df_temp4.CRASH_ID==df_temp2.CRASH_ID)&(df_temp4.UNIT_NBR==df_temp2.UNIT_NBR))

'df_temp5' : all  licensed people charged with overspeeding, and their vehicle information


In [0]:
display(df_temp5.filter(col("VEH_COLOR_ID").isin(list_top10_colors)).filter(col("VEH_LIC_STATE_ID").isin(list_top25_states)))

crash_id_2 unit_nbr_2 PRSN_NBR CHARGE CRASH_ID UNIT_NBR DRVR_LIC_RESTRIC_ID CRASH_ID UNIT_NBR UNIT_DESC_ID VEH_PARKED_FL VEH_HNR_FL VEH_LIC_STATE_ID VIN VEH_MOD_YEAR VEH_COLOR_ID VEH_MAKE_ID VEH_MOD_ID VEH_BODY_STYL_ID EMER_RESPNDR_FL OWNR_ZIP FIN_RESP_PROOF_ID FIN_RESP_TYPE_ID VEH_DMAG_AREA_1_ID VEH_DMAG_SCL_1_ID FORCE_DIR_1_ID VEH_DMAG_AREA_2_ID VEH_DMAG_SCL_2_ID FORCE_DIR_2_ID VEH_INVENTORIED_FL VEH_TRANSP_NAME VEH_TRANSP_DEST CONTRIB_FACTR_1_ID CONTRIB_FACTR_2_ID CONTRIB_FACTR_P1_ID VEH_TRVL_DIR_ID FIRST_HARM_EVT_INV_ID INCAP_INJRY_CNT NONINCAP_INJRY_CNT POSS_INJRY_CNT NON_INJRY_CNT UNKN_INJRY_CNT TOT_INJRY_CNT DEATH_CNT 14842539 3 1 FAILURE TO CONTROL SPEED (ACC) 14842539 3 NONE 14842539 3 MOTOR VEHICLE N N TX JTDBE32K920120327 2002 GRN TOYOTA CAMRY PASSENGER CAR, 4-DOOR N null 1 LIABILITY INSURANCE POLICY BACK END DAMAGE DISTRIBUTED IMPACT DAMAGED 1 MINIMUM 6 FRONT END DAMAGE DISTRIBUTED IMPACT DAMAGED 1 MINIMUM 12 N OWNER DRIVEN AWAY NA NA DRIVER INATTENTION EAST N 0 0 0 1 0 0 0 14850780 1 1 UNSAFE SPEED 14850780 1 NONE 14850780 1 MOTOR VEHICLE N N TX 3N1AB7AP4EY296630 NA WHI NISSAN SENTRA PASSENGER CAR, 4-DOOR N 77856 1 PROOF OF LIABILITY INSURANCE FRONT END DAMAGE CONCENTRATED IMPACT DAMAGED 3 12 FRONT END DAMAGE DISTRIBUTED IMPACT DAMAGED 3 11 N B&D WRECKER SERVICE 5350 RED ROCK RD., FRANKLIN, TX 77856 UNSAFE SPEED NA NA SOUTHEAST Y 0 0 1 0 0 1 0 14851724 1 1 UNSAFE SPEED 14851724 1 OTHER/OUT OF STATE 14851724 1 MOTOR VEHICLE N N TX 1XKYDP9X0FJ431977 NA WHI KENWORTH NA TRUCK TRACTOR N 75206 1 PROOF OF LIABILITY INSURANCE LEFT SIDE AND TOP DAMAGE ROLLOVER EFFECTS DAMAGED 5 9 RIGHT BACK QUARTER DAMAGE ANGULAR IMPACT DAMAGED 2 5 N BOB DOUTHIT AUTOS 1432 S. BARNES ST. PAMPA, TX 79065 UNSAFE SPEED NA NA EAST Y 0 0 0 1 0 0 0 14851724 1 1 UNSAFE SPEED 14851724 1 OTHER/OUT OF STATE 14851724 1 MOTOR VEHICLE N N TX 1XKYDP9X0FJ431977 NA WHI KENWORTH NA TRUCK TRACTOR N 75206 1 PROOF OF LIABILITY INSURANCE LEFT SIDE AND TOP DAMAGE ROLLOVER EFFECTS DAMAGED 5 9 RIGHT BACK QUARTER DAMAGE ANGULAR IMPACT DAMAGED 2 5 N BOB DOUTHIT AUTOS 1432 S. BARNES ST. PAMPA, TX 79065 UNSAFE SPEED NA NA EAST Y 0 0 0 1 0 0 0 14852262 1 1 UNSAFE SPEED 14852262 1 OTHER/OUT OF STATE 14852262 1 MOTOR VEHICLE N N TX 1FTYR14V7XPA88874 1999 TAN FORD RANGER PICKUP N 77624 1 PROOF OF LIABILITY INSURANCE FRONT END (LEFT) DAMAGE PARTIAL CONTACT DAMAGED 1 MINIMUM 11 NA NA NA N null null UNSAFE SPEED NA NA SOUTH Y 0 0 0 1 0 0 0 14864295 1 1 FAIL TO CONTROL SPEED 14864295 1 NONE 14864295 1 MOTOR VEHICLE N N TX 3D7HA18N82G111003 2002 MAR DODGE RAM 1500 PICKUP N 76574 1 PROOF OF LIABILITY INSURANCE LEFT FRONT QUARTER DAMAGE ANGULAR IMPACT DAMAGED 4 11 NA NA NA N NOT TOWED LEFT ON SCENE DRIVER INATTENTION FAILED TO CONTROL SPEED NA WEST Y 0 0 0 1 0 0 0 14870550 1 1 FAILURE TO CONTROL SPEED 14870550 1 NONE 14870550 1 MOTOR VEHICLE N N TX 1FDWF36P25EC70898 2005 WHI FORD F350 TRUCK N 77356 1 PROOF OF LIABILITY INSURANCE BACK END DAMAGE CONCENTRATED IMPACT DAMAGED 1 MINIMUM 12 NA NA NA N null null FAILED TO CONTROL SPEED NA DRIVER INATTENTION EAST Y 0 0 0 1 0 0 0 14871137 1 1 UNSAFE SPEED 14871137 1 WITH CORRECTIVE LENSES 14871137 1 MOTOR VEHICLE N N TX 1FTRF3DT4DEB49497 NA SIL FORD F350 PICKUP N 76548 1 PROOF OF LIABILITY INSURANCE FRONT END DAMAGE DISTRIBUTED IMPACT DAMAGED 1 MINIMUM 12 NA NA NA N null null UNSAFE SPEED IMPAIRED VISIBILITY (EXPLAIN IN NARRATIVE) NA EAST Y 0 0 0 1 0 0 0 14871137 1 1 UNSAFE SPEED 14871137 1 WITH CORRECTIVE LENSES 14871137 1 MOTOR VEHICLE N N TX 1FTRF3DT4DEB49497 NA SIL FORD F350 PICKUP N 76548 1 PROOF OF LIABILITY INSURANCE FRONT END DAMAGE DISTRIBUTED IMPACT DAMAGED 1 MINIMUM 12 NA NA NA N null null UNSAFE SPEED IMPAIRED VISIBILITY (EXPLAIN IN NARRATIVE) NA EAST Y 0 0 0 1 0 0 0 14871431 1 1 FAIL TO CONTROL SPEED 14871431 1 NONE 14871431 1 MOTOR VEHICLE N N TX 4T1BF1FK8EU466647 NA BLU TOYOTA CAMRY PASSENGER CAR, 4-DOOR N 77562 1 PROOF OF LIABILITY INSURANCE RIGHT FRONT QUARTER DAMAGE ANGULAR IMPACT DAMAGED 2 2 RIGHT FRONT QUARTER DAMAGE 

In [0]:
df_temp6=df_temp5.filter(col("VEH_COLOR_ID").isin(list_top10_colors)).filter(col("VEH_LIC_STATE_ID").isin(list_top25_states))

In [0]:
df_temp6.groupBy("VEH_MAKE_ID").count().orderBy(desc("count")).limit(5).show()

+-----------+-----+
|VEH_MAKE_ID|count|
+-----------+-----+
|       FORD| 4455|
|  CHEVROLET| 3843|
|     TOYOTA| 2344|
|      DODGE| 1988|
|      HONDA| 1454|
+-----------+-----+



In [0]:
df_temp6.groupBy("VEH_MAKE_ID").count().orderBy(desc("count")).withColumn("rank",monotonically_increasing_id()+1).select("VEH_MAKE_ID","rank").show(5)

+-----------+----+
|VEH_MAKE_ID|rank|
+-----------+----+
|       FORD|   1|
|  CHEVROLET|   2|
|     TOYOTA|   3|
|      DODGE|   4|
|      HONDA|   5|
+-----------+----+
only showing top 5 rows

